# PRÉSENTATION DU JEU DE LA VIE
Le jeu de la vie est une création de John Conway.

C'est le plus connu des automates cellulaires : une grille de cellules évoluant au cours du temps selon un petit nombre de règles.

Ici, on se place dans une grille simple, faite de carrés, chaque cellule est donc encadrée par 8 autres cellules.

Malgré des règles très simples, le jeu de la vie permet le développement de motifs extrêmement complexes.

# RÈGLES DU JEU DE LA VIE
Les règles de ce jeu sont les suivantes :

- Chaque cellule ne peut avoir que deux état : la vie et la mort.
- Si une cellule en vie n'a qu'une voisine ou aucune, elle meurt de solitude.
- Si une cellule en vie a 4 voisines ou plus, elle meurt de surpopulation.
- Avec 2 ou 3 voisins, une cellule en vie reste en vie.
- Quand exactement 3 cellules vivantes encadrent une quatrième morte, celle-ci renaït à l'étape suivante.

Je vais rester sur une approche à bord ouvert. Si une cellule est à l'extrême droite de la grille, sa voisine de droite sera la cellule à l'extrême gauche et vice versa.

Voici une version faites avec pygame.
- On mets pause avec Espace
- On reset la grille avec R.

In [4]:
import pygame
import sys

# Initialisation de Pygame
pygame.init()

# Paramètres de la grille
cell_size = 20
grid_width, grid_height = 40, 30
grid = [[0] * grid_width for _ in range(grid_height)]
is_running = False

# Couleurs
white = (255, 255, 255)
black = (0, 0, 0)
gray = (200, 200, 200)

# Création de la fenêtre Pygame
width, height = grid_width * cell_size, grid_height * cell_size
screen = pygame.display.set_mode((width, height))
pygame.display.set_caption("Jeu de la Vie")

# Police
font = pygame.font.Font(None, 36)

# Fonction pour dessiner la grille
def draw_grid():
    for y in range(grid_height):
        for x in range(grid_width):
            color = white if grid[y][x] == 0 else black
            pygame.draw.rect(screen, color, (x * cell_size, y * cell_size, cell_size, cell_size), 0)
            pygame.draw.line(screen, gray, (x * cell_size, 0), (x * cell_size, height))
        pygame.draw.line(screen, gray, (0, y * cell_size), (width, y * cell_size))

# Fonction pour mettre à jour la grille selon les règles du jeu de la vie
def update_grid():
    global grid
    new_grid = [[0] * grid_width for _ in range(grid_height)]

    for y in range(grid_height):
        for x in range(grid_width):
            neighbors = sum(grid[(y + i) % grid_height][(x + j) % grid_width] for i in [-1, 0, 1] for j in [-1, 0, 1]) - grid[y][x]
            if grid[y][x] == 1 and (neighbors < 2 or neighbors > 3):
                new_grid[y][x] = 0
            elif grid[y][x] == 0 and neighbors == 3:
                new_grid[y][x] = 1
            else:
                new_grid[y][x] = grid[y][x]

    grid = new_grid

try:
    # Boucle principale
    while True:
        for event in pygame.event.get():
            if event.type == pygame.QUIT:
                pygame.quit()
                sys.exit()
            elif event.type == pygame.MOUSEBUTTONDOWN and event.button == 1:
                x, y = event.pos
                grid[y // cell_size][x // cell_size] = 1 - grid[y // cell_size][x // cell_size]
            elif event.type == pygame.KEYDOWN:
                if event.key == pygame.K_SPACE:
                    is_running = not is_running
                elif event.key == pygame.K_r:
                    grid = [[0] * grid_width for _ in range(grid_height)]

        if is_running:
            update_grid()

        # Dessiner la grille et les lignes
        screen.fill(white if is_running else gray)
        draw_grid()

        # Afficher l'indicateur de mode
        mode_text = "En Pause" if not is_running else "En Cours"
        mode_color = black if is_running else gray
        mode_surface = font.render(mode_text, True, mode_color)
        screen.blit(mode_surface, (10, height - 40))

        # Mettre à jour l'affichage
        pygame.display.flip()

        # Limiter la vitesse de la boucle
        pygame.time.Clock().tick(10)
except SystemExit:
    pass

Et voici une autre version faites avec TKinter.

In [41]:
import tkinter as tk

class GameOfLife:
    def __init__(self, master, cell_size, width=800, height=600, speed=50):
        self.master = master
        self.master.title("Jeu de la Vie")

        self.cell_size = cell_size
        self.width = width
        self.height = height
        self.speed = speed
        self.is_running = False
        self.is_setup = False  # Nouvelle variable pour indiquer si le jeu est en configuration

        self.create_widgets()
        self.create_grid()

    def create_widgets(self):
        self.canvas = tk.Canvas(self.master, width=self.width, height=self.height, bg='white')
        self.canvas.bind("<Button-1>", self.toggle_cell)
        self.canvas.pack()

        self.start_button = tk.Button(self.master, text='Go!', command=self.toggle_simulation)
        self.start_button.pack(side=tk.LEFT, padx=5)
        
        self.stop_button = tk.Button(self.master, text='Stop', command=self.stop_simulation)
        self.stop_button.pack(side=tk.LEFT, padx=5)

        self.reset_button = tk.Button(self.master, text='Reset Grid', command=self.reset_grid)
        self.reset_button.pack(side=tk.LEFT, padx=5)

        self.structure_button1 = tk.Button(self.master, text='Vaisseau', command=self.create_spaceship)
        self.structure_button1.pack(side=tk.LEFT, padx=5)

        self.structure_button2 = tk.Button(self.master, text='Canon', command=self.create_cannon)
        self.structure_button2.pack(side=tk.LEFT, padx=5)

        self.speed_label = tk.Label(self.master, text='Speed (ms):')
        self.speed_label.pack(side=tk.RIGHT)
        
        self.speed_entry = tk.Entry(self.master)
        self.speed_entry.insert(tk.END, str(self.speed))
        self.speed_entry.bind("<Return>", self.change_speed)
        self.speed_entry.pack(side=tk.RIGHT)

        # Label pour afficher l'état du jeu
        self.status_label = tk.Label(self.master, text='Setup')
        self.status_label.pack(side=tk.BOTTOM)

    def create_grid(self):
        self.cells = {}
        for x in range(0, self.width, self.cell_size):
            for y in range(0, self.height, self.cell_size):
                cell_id = self.canvas.create_rectangle(x, y, x + self.cell_size, y + self.cell_size, fill='white')
                self.cells[x, y] = cell_id

    def toggle_cell(self, event):
        x, y = event.x - (event.x % self.cell_size), event.y - (event.y % self.cell_size)
        cell_id = self.cells[x, y]
        fill_color = 'black' if self.canvas.itemcget(cell_id, 'fill') == 'white' else 'white'
        self.canvas.itemconfig(cell_id, fill=fill_color)

    def toggle_simulation(self):
        if self.is_setup:
            self.status_label.config(text='Playing')
            self.is_running = True
            self.run_simulation()
        else:
            self.status_label.config(text='Setup')
            self.is_setup = True

    def run_simulation(self):
        self.play()
        if self.is_running:
            self.master.after(self.speed, self.run_simulation)

    def stop_simulation(self):
        self.is_running = False
        self.status_label.config(text='Setup')

    def play(self):
        new_cells = {}
        for x in range(0, self.width, self.cell_size):
            for y in range(0, self.height, self.cell_size):
                neighbors = self.count_neighbors(x, y)
                cell_id = self.cells[x, y]

                if self.canvas.itemcget(cell_id, 'fill') == 'white' and neighbors == 3:
                    new_cells[x, y] = 'black'
                elif self.canvas.itemcget(cell_id, 'fill') == 'black' and (neighbors < 2 or neighbors > 3):
                    new_cells[x, y] = 'white'
                else:
                    new_cells[x, y] = self.canvas.itemcget(cell_id, 'fill')

        for x, y in new_cells:
            cell_id = self.cells[x, y]
            self.canvas.itemconfig(cell_id, fill=new_cells[x, y])

    def count_neighbors(self, x, y):
        neighbors = 0
        for i in [-self.cell_size, 0, self.cell_size]:
            for j in [-self.cell_size, 0, self.cell_size]:
                if i == j == 0:
                    continue
                neighbor_x, neighbor_y = (x + i) % self.width, (y + j) % self.height
                cell_id = self.cells[neighbor_x, neighbor_y]
                if self.canvas.itemcget(cell_id, 'fill') == 'black':
                    neighbors += 1
        return neighbors

    def reset_grid(self):
        self.is_setup = False
        self.status_label.config(text='Setup')
        for x in range(0, self.width, self.cell_size):
            for y in range(0, self.height, self.cell_size):
                cell_id = self.cells[x, y]
                self.canvas.itemconfig(cell_id, fill='white')

    def create_spaceship(self):
        # Exemple : Glider (planeur)
        self.reset_grid()  # Réinitialiser la grille avant de créer un motif
        self.canvas.itemconfig(self.cells[20, 20], fill='black')
        self.canvas.itemconfig(self.cells[40, 20], fill='black')
        self.canvas.itemconfig(self.cells[60, 20], fill='black')
        self.canvas.itemconfig(self.cells[60, 40], fill='black')
        self.canvas.itemconfig(self.cells[40, 60], fill='black')

    def create_cannon(self):
        # Exemple : Gosper Glider Gun
        self.reset_grid()  # Réinitialiser la grille avant de créer un motif
        self.canvas.itemconfig(self.cells[0, 5*self.cell_size], fill='black')
        self.canvas.itemconfig(self.cells[0, 6*self.cell_size], fill='black')
        self.canvas.itemconfig(self.cells[1*self.cell_size, 5*self.cell_size], fill='black')
        self.canvas.itemconfig(self.cells[1*self.cell_size, 6*self.cell_size], fill='black')
        self.canvas.itemconfig(self.cells[10*self.cell_size, 5*self.cell_size], fill='black')
        self.canvas.itemconfig(self.cells[10*self.cell_size, 6*self.cell_size], fill='black')
        self.canvas.itemconfig(self.cells[10*self.cell_size, 7*self.cell_size], fill='black')
        self.canvas.itemconfig(self.cells[11*self.cell_size, 4*self.cell_size], fill='black')
        self.canvas.itemconfig(self.cells[11*self.cell_size, 8*self.cell_size], fill='black')
        self.canvas.itemconfig(self.cells[12*self.cell_size, 3*self.cell_size], fill='black')
        self.canvas.itemconfig(self.cells[12*self.cell_size, 9*self.cell_size], fill='black')
        self.canvas.itemconfig(self.cells[13*self.cell_size, 3*self.cell_size], fill='black')
        self.canvas.itemconfig(self.cells[13*self.cell_size, 9*self.cell_size], fill='black')
        self.canvas.itemconfig(self.cells[14*self.cell_size, 6*self.cell_size], fill='black')
        self.canvas.itemconfig(self.cells[15*self.cell_size, 4*self.cell_size], fill='black')
        self.canvas.itemconfig(self.cells[15*self.cell_size, 8*self.cell_size], fill='black')
        self.canvas.itemconfig(self.cells[16*self.cell_size, 5*self.cell_size], fill='black')
        self.canvas.itemconfig(self.cells[16*self.cell_size, 6*self.cell_size], fill='black')
        self.canvas.itemconfig(self.cells[16*self.cell_size, 7*self.cell_size], fill='black')
        self.canvas.itemconfig(self.cells[17*self.cell_size, 6*self.cell_size], fill='black')
        self.canvas.itemconfig(self.cells[20*self.cell_size, 3*self.cell_size], fill='black')
        self.canvas.itemconfig(self.cells[20*self.cell_size, 4*self.cell_size], fill='black')
        self.canvas.itemconfig(self.cells[20*self.cell_size, 5*self.cell_size], fill='black')
        self.canvas.itemconfig(self.cells[21*self.cell_size, 3*self.cell_size], fill='black')
        self.canvas.itemconfig(self.cells[21*self.cell_size, 4*self.cell_size], fill='black')
        self.canvas.itemconfig(self.cells[21*self.cell_size, 5*self.cell_size], fill='black')
        self.canvas.itemconfig(self.cells[22*self.cell_size, 2*self.cell_size], fill='black')
        self.canvas.itemconfig(self.cells[22*self.cell_size, 6*self.cell_size], fill='black')
        self.canvas.itemconfig(self.cells[24*self.cell_size, 1*self.cell_size], fill='black')
        self.canvas.itemconfig(self.cells[24*self.cell_size, 2*self.cell_size], fill='black')
        self.canvas.itemconfig(self.cells[24*self.cell_size, 6*self.cell_size], fill='black')
        self.canvas.itemconfig(self.cells[24*self.cell_size, 7*self.cell_size], fill='black')
        self.canvas.itemconfig(self.cells[34*self.cell_size, 3*self.cell_size], fill='black')
        self.canvas.itemconfig(self.cells[34*self.cell_size, 4*self.cell_size], fill='black')
        self.canvas.itemconfig(self.cells[35*self.cell_size, 3*self.cell_size], fill='black')
        self.canvas.itemconfig(self.cells[35*self.cell_size, 4*self.cell_size], fill='black')

    def change_speed(self, event):
        try:
            self.speed = int(self.speed_entry.get())
        except ValueError:
            pass

if __name__ == "__main__":
    root = tk.Tk()
    game = GameOfLife(root, cell_size=20)
    root.mainloop()


580
0
20
580
20
580
0
20
0
20
40
0
40
0
20
40
20
40
60
20
60
20
40
60
40
60
80
40
80
40
60
80
60
80
100
60
100
60
80
100
80
100
120
80
120
80
100
120
100
120
140
100
140
100
120
140
120
140
160
120
160
120
140
160
140
160
180
140
180
140
160
180
160
180
200
160
200
160
180
200
180
200
220
180
220
180
200
220
200
220
240
200
240
200
220
240
220
240
260
220
260
220
240
260
240
260
280
240
280
240
260
280
260
280
300
260
300
260
280
300
280
300
320
280
320
280
300
320
300
320
340
300
340
300
320
340
320
340
360
320
360
320
340
360
340
360
380
340
380
340
360
380
360
380
400
360
400
360
380
400
380
400
420
380
420
380
400
420
400
420
440
400
440
400
420
440
420
440
460
420
460
420
440
460
440
460
480
440
480
440
460
480
460
480
500
460
500
460
480
500
480
500
520
480
520
480
500
520
500
520
540
500
540
500
520
540
520
540
560
520
560
520
540
560
540
560
580
540
580
540
560
580
560
580
0
560
0
560
580
0
580
0
20
580
20
580
0
20
0
20
40
0
40
0
20
40
20
40
60
20
60
20
40
60
40
60
80
40
80
40
